In [1]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Fri Feb  4 15:33:17 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.57.02    Driver Version: 470.57.02    CUDA Version: 11.4     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100S-PCI...  Off  | 00000000:00:08.0 Off |                    0 |
| N/A   34C    P0    54W / 250W |      0MiB / 32510MiB |    100%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [8]:
from datasets import concatenate_datasets, load_dataset, load_metric, Audio

cv_cs = load_dataset("mozilla-foundation/common_voice_8_0", "cs", split="train+validation", use_auth_token=True)
cv_sk = load_dataset("mozilla-foundation/common_voice_8_0", "sk", split="train+validation", use_auth_token=True)
cv_pl = load_dataset("mozilla-foundation/common_voice_8_0", "pl", split="train+validation", use_auth_token=True)
cv_sl = load_dataset("mozilla-foundation/common_voice_8_0", "sl", split="train+validation", use_auth_token=True)
cv_hsb = load_dataset("mozilla-foundation/common_voice_8_0", "hsb", split="train+validation", use_auth_token=True)
common_voice_train = concatenate_datasets([cv_cs, cv_sk, cv_pl, cv_sl, cv_hsb])
common_voice_train = common_voice_train.shuffle()

def begin(_, i):
    return i < 1000
cv_cs_test = load_dataset("mozilla-foundation/common_voice_8_0", "cs", split="test", use_auth_token=True).filter(begin, with_indices=True)
cv_sk_test = load_dataset("mozilla-foundation/common_voice_8_0", "sk", split="test", use_auth_token=True).filter(begin, with_indices=True)
cv_pl_test = load_dataset("mozilla-foundation/common_voice_8_0", "pl", split="test", use_auth_token=True).filter(begin, with_indices=True)
cv_sl_test = load_dataset("mozilla-foundation/common_voice_8_0", "sl", split="test", use_auth_token=True).filter(begin, with_indices=True)
cv_hsb_test = load_dataset("mozilla-foundation/common_voice_8_0", "hsb", split="test", use_auth_token=True).filter(begin, with_indices=True)
common_voice_test = interleave_datasets([cv_cs_test, cv_sk_test, cv_pl_test, cv_sl_test, cv_hsb_test])
len(common_voice_train)


Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/cs/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)
Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/sk/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)
Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/pl/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)
Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/sl/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)
Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/hsb/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)
Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/cs/8.0

51319

In [9]:
common_voice_train = common_voice_train.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])
common_voice_test = common_voice_test.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])

In [10]:
from datasets import ClassLabel
import random
import pandas as pd
from IPython.display import display, HTML

def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)
    
    df = pd.DataFrame(dataset[picks])
    display(HTML(df.to_html()))

In [11]:
show_random_elements(common_voice_train.remove_columns(["path", "audio"]), num_examples=10)

In [12]:
import re
chars_to_remove_regex = '[\,\?\.\!\-\;\:\/\"\“\„\%\”\�\–\'\`\«\»\—\’\…\³\'̌]'


CHARS = {
    'ü': 'ue',
    'ö': 'oe',
    'ï': 'i',
    'ë': 'e',
    'ã': 'a',
    'à': 'á',
    'ø': 'o',
    'å': 'ó',
    'î': 'i',
    'ñ': 'ň',
    'ç': 's',
    'ć': 'č',
    'þ': 't',
    'ß': 'ss',
    'ę': 'en',
    'ą': 'an',
    'æ': 'ae',
  }

def replace_chars(sentence):
  result = ''
  for ch in sentence:
    new = CHARS[ch] if ch in CHARS else ch
    result += new

  return result


def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, ' ', batch["sentence"]).lower()
    batch["sentence"] = replace_chars(batch['sentence'])
    batch["sentence"] = " ".join([char for char in batch["sentence"].split(" ") if char != ""])
    return batch


In [13]:
batch = {"sentence": "Jak se vede, /Björne?"}
remove_special_characters(batch)

{'sentence': 'jak se vede bjoerne'}

In [14]:
show_random_elements(common_voice_train.map(remove_special_characters).remove_columns(["path", "audio"]), num_examples=10)

0ex [00:00, ?ex/s]

In [15]:
common_voice_train = common_voice_train.map(remove_special_characters)
common_voice_test = common_voice_test.map(remove_special_characters)

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/cs/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8/cache-43b574eb63589540.arrow


0ex [00:00, ?ex/s]

In [16]:
show_random_elements(common_voice_train.remove_columns(["path","audio"]))

In [17]:
def extract_all_chars(batch):
  all_text = " ".join(batch["sentence"])
  vocab = list(set(all_text))
  return {"vocab": [vocab], "all_text": [all_text]}

In [18]:
vocab_train = common_voice_train.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_train.column_names)
vocab_test = common_voice_test.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_test.column_names)

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

In [19]:
vocab_list = list(set(vocab_train["vocab"][0]) | set(vocab_test["vocab"][0]))

In [20]:
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}
vocab_dict

{' ': 0,
 'a': 1,
 'b': 2,
 'c': 3,
 'd': 4,
 'e': 5,
 'f': 6,
 'g': 7,
 'h': 8,
 'i': 9,
 'j': 10,
 'k': 11,
 'l': 12,
 'm': 13,
 'n': 14,
 'o': 15,
 'p': 16,
 'q': 17,
 'r': 18,
 's': 19,
 't': 20,
 'u': 21,
 'v': 22,
 'w': 23,
 'x': 24,
 'y': 25,
 'z': 26,
 'á': 27,
 'ä': 28,
 'è': 29,
 'é': 30,
 'í': 31,
 'ó': 32,
 'ô': 33,
 'ú': 34,
 'ý': 35,
 'č': 36,
 'ď': 37,
 'ě': 38,
 'ĺ': 39,
 'ľ': 40,
 'ł': 41,
 'ń': 42,
 'ň': 43,
 'ŕ': 44,
 'ř': 45,
 'ś': 46,
 'š': 47,
 'ť': 48,
 'ů': 49,
 'ź': 50,
 'ż': 51,
 'ž': 52}

In [21]:
vocab_dict["|"] = vocab_dict[" "]
del vocab_dict[" "]

In [22]:
vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)
len(vocab_dict)

55

In [23]:
import json
with open('vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)

In [24]:
from transformers import Wav2Vec2CTCTokenizer

tokenizer = Wav2Vec2CTCTokenizer.from_pretrained("./", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")

file ./config.json not found
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [25]:
repo_name = "wav2vec2-xls-r-300m-west-slavic-cv8"

In [26]:
from transformers import Wav2Vec2FeatureExtractor

feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)

In [27]:
from transformers import Wav2Vec2Processor

processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [28]:
# save tokenizer to folder
processor.save_pretrained(repo_name)

In [29]:
common_voice_train[0]["path"]

'cv-corpus-8.0-2022-01-19/cs/clips/common_voice_cs_20715969.mp3'

In [30]:
common_voice_train[0]["audio"]

{'path': 'cv-corpus-8.0-2022-01-19/cs/clips/common_voice_cs_20715969.mp3',
 'array': array([ 0.0000000e+00,  0.0000000e+00,  0.0000000e+00, ...,
        -2.4139881e-05, -1.6212463e-05, -3.5226345e-05], dtype=float32),
 'sampling_rate': 48000}

In [31]:
common_voice_train = common_voice_train.cast_column("audio", Audio(sampling_rate=16_000))
common_voice_test = common_voice_test.cast_column("audio", Audio(sampling_rate=16_000))

In [32]:
common_voice_train[0]["audio"]

{'path': 'cv-corpus-8.0-2022-01-19/cs/clips/common_voice_cs_20715969.mp3',
 'array': array([ 0.0000000e+00,  0.0000000e+00,  0.0000000e+00, ...,
        -4.3994612e-05,  1.2149939e-06, -2.9500850e-05], dtype=float32),
 'sampling_rate': 16000}

In [33]:
import IPython.display as ipd
import numpy as np
import random

rand_int = random.randint(0, len(common_voice_train)-1)

print(common_voice_train[rand_int]["sentence"])
ipd.Audio(data=common_voice_train[rand_int]["audio"]["array"], autoplay=True, rate=16000)

po pierwsze afryka żyje w wieku globalnej gospodarki i globalizacji


In [34]:
rand_int = random.randint(0, len(common_voice_train)-1)

print("Target text:", common_voice_train[rand_int]["sentence"])
print("Input array shape:", common_voice_train[rand_int]["audio"]["array"].shape)
print("Sampling rate:", common_voice_train[rand_int]["audio"]["sampling_rate"])

Target text: několikrát byl v boji raněn
Input array shape: (51840,)
Sampling rate: 16000


In [35]:
def prepare_dataset(batch):
    audio = batch["audio"]

    # batched output is "un-batched"
    batch["input_values"] = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [36]:
common_voice_train = common_voice_train.map(prepare_dataset, remove_columns=common_voice_train.column_names)
common_voice_test = common_voice_test.map(prepare_dataset, remove_columns=common_voice_test.column_names)

0ex [00:00, ?ex/s]

0ex [00:00, ?ex/s]

In [37]:
import torch

from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union

@dataclass
class DataCollatorCTCWithPadding:
    """
    Data collator that will dynamically pad the inputs received.
    Args:
        processor (:class:`~transformers.Wav2Vec2Processor`)
            The processor used for proccessing the data.
        padding (:obj:`bool`, :obj:`str` or :class:`~transformers.tokenization_utils_base.PaddingStrategy`, `optional`, defaults to :obj:`True`):
            Select a strategy to pad the returned sequences (according to the model's padding side and padding index)
            among:
            * :obj:`True` or :obj:`'longest'`: Pad to the longest sequence in the batch (or no padding if only a single
              sequence if provided).
            * :obj:`'max_length'`: Pad to a maximum length specified with the argument :obj:`max_length` or to the
              maximum acceptable input length for the model if that argument is not provided.
            * :obj:`False` or :obj:`'do_not_pad'` (default): No padding (i.e., can output a batch with sequences of
              different lengths).
    """

    processor: Wav2Vec2Processor
    padding: Union[bool, str] = True

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lenghts and need
        # different padding methods
        input_features = [{"input_values": feature["input_values"]} for feature in features]
        label_features = [{"input_ids": feature["labels"]} for feature in features]

        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            return_tensors="pt",
        )
        with self.processor.as_target_processor():
            labels_batch = self.processor.pad(
                label_features,
                padding=self.padding,
                return_tensors="pt",
            )

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch["labels"] = labels

        return batch

In [38]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

In [39]:
wer_metric = load_metric("wer")
cer_metric = load_metric("cer")
metrics = [wer_metric, cer_metric]

In [40]:
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_ids = np.argmax(pred_logits, axis=-1)

    pred.label_ids[pred.label_ids == -100] = processor.tokenizer.pad_token_id

    pred_str = processor.batch_decode(pred_ids)
    # we do not want to group tokens when computing the metrics
    label_str = processor.batch_decode(pred.label_ids, group_tokens=False)

    wer = wer_metric.compute(predictions=pred_str, references=label_str)
    cer = cer_metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer, "cer": cer}

In [43]:
from transformers import Wav2Vec2ForCTC

model = Wav2Vec2ForCTC.from_pretrained(
    #"facebook/wav2vec2-xls-r-300m", 
    'comodoro/'+repo_name,
    attention_dropout=0.1,
    hidden_dropout=0.1,
    feat_proj_dropout=0.0,
    mask_time_prob=0.05,
    layerdrop=0.1,
    ctc_loss_reduction="mean", 
    pad_token_id=processor.tokenizer.pad_token_id,
    vocab_size=len(processor.tokenizer),
)

In [44]:
model.freeze_feature_extractor()

/opt/conda/lib/python3.8/site-packages/transformers/models/wav2vec2/modeling_wav2vec2.py:1680: FutureWarning: The method `freeze_feature_extractor` is deprecated and will be removed in Transformers v5.Please use the equivalent `freeze_feature_encoder` method instead.
  warnings.warn(


In [45]:
from transformers import TrainingArguments

training_args = TrainingArguments(
  output_dir=repo_name,
  group_by_length=True,
  per_device_train_batch_size=16,
  per_device_eval_batch_size=16,
  gradient_accumulation_steps=1,
  eval_accumulation_steps=1,
  evaluation_strategy="steps",
  num_train_epochs=30,
  gradient_checkpointing=True,
  fp16=True,
  save_steps=400,
  eval_steps=400,
  logging_steps=400,
  learning_rate=1e-3,
  warmup_steps=500,
  save_total_limit=2,
  report_to="tensorboard"
)

In [46]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    data_collator=data_collator,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=common_voice_train,
    eval_dataset=common_voice_test,
    tokenizer=processor.feature_extractor,
)

Using amp half precision backend


In [47]:
trainer.train()

The following columns in the training set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
/opt/conda/lib/python3.8/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use thePyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 51319
  Num Epochs = 30
  Instantaneous batch size per device = 16
  Total train batch size (w. parallel, distributed & accumulation) = 16
  Gradient Accumulation steps = 1
  Total optimization steps = 96240


The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 2090
  Batch size = 16
Saving model checkpoint to wav2vec2-xls-r-300m-west-slavic-cv8/checkpoint-400
Configuration saved in wav2vec2-xls-r-300m-west-slavic-cv8/checkpoint-400/config.json
Model weights saved in wav2vec2-xls-r-300m-west-slavic-cv8/checkpoint-400/pytorch_model.bin
Configuration saved in wav2vec2-xls-r-300m-west-slavic-cv8/checkpoint-400/preprocessor_config.json
Deleting older checkpoint [wav2vec2-xls-r-300m-west-slavic-cv8/checkpoint-15600] due to args.save_total_limit
The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 2090
  Batch size = 16
Saving model checkpoint to wav2vec2-xls-r-300m-west-slavic-cv8/checkpoint-800
Configuration saved in 

KeyboardInterrupt: 

In [48]:
trainer.create_model_card()

Dropping the following result as it does not have all the necessary fields:
{}


In [ ]:
model.push_to_hub(repo_url='https://huggingface.co/comodoro/wav2vec2-xls-r-300m-west-slavic-cv8')

In [ ]:
!pwd